In [1]:
from Bio import Entrez
import GEOparse
import pandas as pd
import os
import polars as pl
import mysql.connector
import download_files
import preprocess_functions
import insert_tables
from mysql.connector import errorcode
import requests

In [2]:
#Define the paths where GDS files and GPL files are stored
gds_path="../data/gds"
gpl_path="../data/gpl"

In [3]:
#Parse GDS files and extract the expression values data, the samples annotation and the metadata
expression_df, annotation_df, metadata_df=preprocess_functions.fetch_gds_data(gds_path)

08-Jul-2024 11:22:11 INFO GEOparse - Parsing ../data/gds/GDS1050.soft: 
08-Jul-2024 11:22:11 DEBUG GEOparse - DATABASE: Geo
08-Jul-2024 11:22:11 DEBUG GEOparse - DATASET: GDS1050
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS1050_1
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS1050_2
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS1050_3
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS1050_4
08-Jul-2024 11:22:11 DEBUG GEOparse - DATASET: GDS1050
08-Jul-2024 11:22:11 INFO GEOparse - Parsing ../data/gds/GDS5211.soft: 
08-Jul-2024 11:22:11 DEBUG GEOparse - DATABASE: Geo
08-Jul-2024 11:22:11 DEBUG GEOparse - DATASET: GDS5211
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS5211_1
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS5211_2
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS5211_3
08-Jul-2024 11:22:11 DEBUG GEOparse - SUBSET: GDS5211_4
08-Jul-2024 11:22:11 DEBUG GEOparse - DATASET: GDS5211
08-Jul-2024 11:22:11 INFO GEOparse - Parsing ../data/gds/GDS1563.soft: 
08-Jul-2024 

In [ ]:
#Define the UMLS API key needed to extract CUIs
apikey='{UMLS_API_pass}' #The API key required to use the UMLS API. 

In [4]:
#Replace null values with '' to avoid errors processing the data
annotation_df['tissue']=annotation_df['tissue'].fillna('')
annotation_df['cell_type']=annotation_df['cell_type'].fillna('')
for column in annotation_df.columns:
        annotation_df[column] = annotation_df[column].fillna('')

#Process disease state column
proc_dis_state=preprocess_functions.process_disease_state(annotation_df)

#Extract tissue and cell type terms CUIs to standardize data
different_tissue_cuis=preprocess_functions.extract_cuis(apikey,proc_dis_state,'tissue')
different_cell_type_cuis=preprocess_functions.extract_cuis(apikey,proc_dis_state,'cell_type')

# Replace the tissue and cell type terms with its corresponding CUI
processed_annotation = proc_dis_state.copy()
for tissue in processed_annotation['tissue']:
    if tissue in different_tissue_cuis:
       cui = different_tissue_cuis[tissue]
       processed_annotation.loc[processed_annotation['tissue'] == tissue, "tissue"] = cui
for cell in processed_annotation['cell_type']:
    if cell in different_cell_type_cuis:
        cui = different_cell_type_cuis[cell]
        processed_annotation.loc[processed_annotation['cell_type'] == cell, "cell_type"] = cui

In [5]:
processed_annotation.head()

gsm_id      agent disease_state   gds_id age cell_type individual gender  \
0  GSM27536  untreated             d  GDS1050                                   
1  GSM27537  untreated             d  GDS1050                                   
2  GSM27538  untreated             d  GDS1050                                   
3  GSM27540  untreated             d  GDS1050                                   
4  GSM27541  untreated             d  GDS1050                                   

  tissue specimen other genotype time cell line development_stage infection  
0                                                                            
1                                                                            
2                                                                            
3                                                                            
4

In [9]:
#Extract the info about the top 10 diseases more related to genes
tsv_file='../data/raw/top10_genecount_disease.tsv'
top10_diseases=download_files.extract_tsv(tsv_file)
top1_disease=top10_diseases['disease_id'].head(1).tolist()

#Select only the GDSs from the top 1 disease more related to genes
csv_file='../results/disease_gds.csv'
diseases_gds=pd.read_csv(csv_file)
filtered_gds=diseases_gds.loc[diseases_gds['disease_id'].isin(top1_disease)]
filtered_gds

disease_id   gds_id
105   C0002395  GDS4136
106   C0002395  GDS4135
107   C0002395  GDS4128
108   C0002395  GDS2519
109   C0002395  GDS2795
110   C0002395   GDS810

In [10]:
#Mark the info from the selected GDSs with a flag
processed_annotation['flag']=processed_annotation['gds_id'].isin(filtered_gds['gds_id']).astype(int)
processed_annotation[processed_annotation['flag']==1]

gsm_id agent disease_state   gds_id           age cell_type  \
13    GSM697332                   d  GDS4136  65 years old             
14    GSM697312                   c  GDS4136  75 years old             
15    GSM697327                   d  GDS4136  79 years old             
16    GSM697334                   d  GDS4136  79 years old             
17    GSM697336                   d  GDS4136  79 years old             
...         ...   ...           ...      ...           ...       ...   
2261  GSM735110                   d  GDS4135                           
2262  GSM735111                   d  GDS4135                           
2263  GSM735106                   d  GDS4135                           
2264  GSM735107                   d  GDS4135                           
2265  GSM735108                   d  GDS4135                           

     individual gender tissue specimen other   genotype time cell line  \
13                                                                       
14                                                                       
15                                                                       
16                                                                       
17                                                                       
...         ...    ...    ...      ...   ...        ...  ...       ...   
2261                                          ApoE ε4 -                  
2262                                          ApoE ε4 -                  
2263                                          ApoE ε4 +                  
2264                                          ApoE ε4 +                  
2265                                          ApoE ε4 +                  

     development_stage infection  flag  
13                                   1  
14                                   1  
15                                   1  
16                                   1  
17                                   1  
...                ...       ...   ...  
2261                                 1  
2262                                 1  
2263                                 1  
2264                                 1  
2265                                 1  

[222 rows x 17 columns]

In [13]:
#Filter the expression dataframe to include only the entries for the selected GDSs
expression_filtered = expression_df[expression_df['gds_id'].isin(filtered_gds['gds_id'])]

#Additional filter to remove expression measurements that do not correspond to actual genes
expression_filtered = expression_filtered[expression_filtered['gene_symbol'] != '--Control']

In [13]:
#The connection details needed to insert data into the database
host = "{host}"  # Host where the MySQL server is located. Example: 'localhost' or '127.0.0.1'
user = "{user_name}"  # Username for accessing the MySQL database. Example: 'root' or 'my_user'
password = "{password}"  # Password for the MySQL user. Ensure to use a secure password for database access.
database = "{database}"  # Name of the database to connect to. Example: 'disnet_biolayer'
port = "{port}"  # Port number for the MySQL server. Default is 3306, but it may vary depending on the setup.

#Get the different GDS IDs
different_gds_ids=annotation_df['gds_id'].unique()

In [18]:
# Initialize the connection variable to None
conn = None

try:
    # Attempt to establish a connection to the MySQL database
    conn = mysql.connector.connect(
        host=host,
        user=user,
        password=password,
        database=database,
        port=port
    )

    # Insert GDS metadata into the database
    insert_tables.insert_gds_metadata(conn, metadata_df)

    # Iterate over different GDS IDs to insert annotations
    for gds_id in different_gds_ids:
        # Filter annotation data for the current GDS ID
        annotation_subset = annotation_df[annotation_df['gds_id'] == gds_id]
        # Insert raw annotation data into the database
        insert_tables.insert_raw_annot(conn, annotation_subset)

        # Filter processed annotation data for the current GDS ID
        annot_subset = processed_annotation[processed_annotation['gds_id'] == gds_id]
        # Insert processed annotation data into the database
        insert_tables.insert_processed_annot(conn, annot_subset)

# Handle any MySQL errors that occur during the connection or insertion process
except mysql.connector.Error as err:
    print(f"Error connecting to MySQL: {err}")

# Ensure the connection is closed properly even if an error occurs
finally:
    if conn and conn.is_connected():
        conn.close()

In [ ]:
# Initialize the connection variable to None
conn = None

try:
    # Attempt to establish a connection to the MySQL database
    conn = mysql.connector.connect(
        host=host,
        user=user,
        password=password,
        database=database,
        port=port
    )
        # Iterate over different GDS IDs to insert expression values
        for gds_id in different_gds_ids:
            # Filter expression values data for the current GDS ID
            values_subset = expression_filtered[expression_filtered['gds_id'] == gds_id]

            # Insert expression values data into the database
            insert_tables.insert_values(conn, values_subset)
    
# Handle any MySQL errors that occur during the connection or insertion process
except mysql.connector.Error as err:
        print(f"Error connecting to MySQL: {err}")

# Ensure the connection is closed properly even if an error occurs
finally:
        if conn and conn.is_connected():
            conn.close()